In [ ]:
# write a flask api to call the stream pipeline to store continous data into the json file, where constrains are not to store the data into json once which is already existed.
def dssa_json(self):
    body = {
        "query": {"match_all": {}}
    }
    index_name = "daily_signup_stats_accounts_v3"
    res = self.es.search(index=index_name, body=body, size=10000)
    hits = res['hits']['hits']
    response = {}

    for hit in hits:
        source = hit['_source']
        report_date = source['report_date']
        date_obj = datetime.datetime.strptime(report_date, '%Y-%m-%dT%H:%M:%S.%fZ')
        year = str(date_obj.year)
        month = date_obj.strftime("%B")
        day = report_date.split('T')[0]

        for key, value in source.items():
            if key.endswith('_user_from'):
                user_id = key.replace('_user_from', '')
                count = value

                if user_id not in response:
                    response[user_id] = {
                        day: count,
                        "partner_sum_total": count,
                        "years": {year: {month: count, "partner_year_count": count}}
                    }
                else:
                    if day not in response[user_id]:
                        response[user_id][day] = count
                    else:
                        response[user_id][day] += count

                    response[user_id]["partner_sum_total"] += count

                    if year not in response[user_id]["years"]:
                        response[user_id]["years"][year] = {"partner_year_count": 0}
                    if month not in response[user_id]["years"][year]:
                        response[user_id]["years"][year][month] = 0

                    response[user_id]["years"][year][month] += count
                    response[user_id]["years"][year]["partner_year_count"] += count

            if key.endswith('_account_type'):
                type_id = key.replace('_account_type', '')
                count = value

                if type_id not in response:
                    response[type_id] = {
                        day: count,
                        "acctype_sum_total": count,
                        "years": {year: {month: count, "acctype_year_count": count}}
                    }
                else:
                    if day not in response[type_id]:
                        response[type_id][day] = count
                    else:
                        response[type_id][day] += count

                    response[type_id]["acctype_sum_total"] += count

                    if year not in response[type_id]["years"]:
                        response[type_id]["years"][year] = {"acctype_year_count": 0}
                    if month not in response[type_id]["years"][year]:
                        response[type_id]["years"][year][month] = 0

                    response[type_id]["years"][year][month] += count
                    response[type_id]["years"][year]["acctype_year_count"] += count
    
    result = {STATUS:SUCCESS, RESPONSE:response}
    return result